In [36]:
install.packages("writexl")
install.packages("lmerTest")


The downloaded binary packages are in
	/var/folders/1m/g73y8g1d17s_z9d8k_jxxsw00000gn/T//RtmpSUZKAA/downloaded_packages

The downloaded binary packages are in
	/var/folders/1m/g73y8g1d17s_z9d8k_jxxsw00000gn/T//RtmpSUZKAA/downloaded_packages


# Κλινικά Ερωτήματα
Μπορεί κάποιος συνδυασμός χαρακτηριστικών φωνής (σε on ή off) να προβλέπει την βαρύτητα ή το στάδιο της νόσου όπως αυτή ορίζεται με διάφορους τρόπους:

- **H&Υ**:
  - Είτε ως δυαδική μεταβλητή (>= 3 ή < 3)
  - Είτε με πολλαπλές τιμές (1, 2, 3, 4)
  
- **Την παρουσία ή όχι διακυμάνσεων**:
  - Fluctuations == “Yes”

- **Την παρουσία ή όχι υπερκινησιών αιχμής-δόσης**:
  - Dyskinesia == “Yes”

- **Την παρουσία άμεσης απάντησης στη θεραπεία (short-term levodopa response)**:
  - Όπως αυτή αντανακλάται στο βαθμό βελτίωσης του UPDRS από OFF σε ΟΝ
    - Ποσοτικά: UDPRS_III_dif_%
    - Ποιοτικά: UPDRS_III_dif_class == “Excellent”, “Suboptimal”, “Poor”


--- 0. Πειραματικό Πλαίσιο και Μεθοδολογία Ανάλυσης ---

Το συγκεκριμένο R script έχει σκοπό να εξετάσει αν τα ηχητικά χαρακτηριστικά της φωνής μπορούν να προβλέψουν βασικές κλινικές μεταβλητές ασθενών με Πάρκινσον.
Χρησιμοποιούμε ένα ενιαίο αρχείο Excel ("Patient_Sorted_Updated_Final_Extracted_Features.xlsx") που περιλαμβάνει τα δεδομένα όλων των ασθενών, τόσο από την κατάσταση "ON" (υπό φαρμακευτική αγωγή)όσο και "OFF" (χωρίς αγωγή).

Η ανάλυση **δεν διαχωρίζει τις δύο καταστάσεις** – τα δεδομένα εξετάζονται όλα μαζί.
Για κάθε φωνητικό task και κάθε κλινική μεταβλητή (π.χ. H&Y, Fluctuations, Dyskinesia, UPDRS),το script εφαρμόζει γραμμικά μοντέλα (LM) ή μικτά γραμμικά μοντέλα (LMM), ανάλογα με τα δεδομένα.
Από τα μοντέλα εξάγονται οι στατιστικοί δείκτες (συντελεστές, standard error, t-value, p-value)για κάθε ακουστικό χαρακτηριστικό.

**Τα χαρακτηριστικά με χαμηλό p-value (π.χ. < 0.05)** θεωρούνται στατιστικά σημαντικά και μπορούν να χρησιμοποιηθούν σε επόμενα στάδια (π.χ. επιλογή χαρακτηριστικών, ML, εντοπισμός βιοδεικτών).
Στο τέλος, όλα τα αποτελέσματα αποθηκεύονται σε αρχείο Excel("summary_all.xlsx") για εύκολη ανάλυση.

In [37]:
# --- 1. Φόρτωση Απαραίτητων Βιβλιοθηκών ---
library(writexl)
library(readxl)
library(lmerTest)
library(dplyr)

# --- 2. Φόρτωση και Προετοιμασία Δεδομένων ---
# Ορισμός της διαδρομής του αρχείου για το κύριο σύνολο δεδομένων
file_path <- "Patient_Sorted_Updated_Final_Extracted_Features.xlsx"
data <- read_excel(file_path)

# Ορισμός βοηθητικής συνάρτησης για το φιλτράρισμα του κύριου data frame
filter_data <- function(data, file_names = NULL) {
  if (!is.null(file_names)) {
    data <- data[data$file_name %in% file_names, ]
  }
  return(data)
}

# Μεταβλητές εξάρτησης που χρησιμοποιούνται για να απαντηθούν τα ερωτήματα που έχουμε 
dependent_variables <- c("H_Y_binary", "Fluctuations", "Dyskinesia", "UPDRS_III_dif_class", "UPDRS_III_dif_per")

# Ορισμός των φωνητικών tasks (εργασιών). Κάθε task είναι μια ομάδα από μία ή περισσότερες μεμονωμένες ασκήσεις (αρχεία .wav).
# Αυτή η δομή λίστας επιτρέπει την ανάλυση των ασκήσεων τόσο μεμονωμένα όσο και ως μέρος ενός ευρύτερου task
tasks <- list(
  task1 = c("a1.wav", "a2.wav", "a3.wav", "z1.wav", "z2.wav", "z3.wav", "s1.wav", "s2.wav", "s3.wav"),
  task2 = c("sakis.wav", "say.wav", "school.wav", "wind.wav", "yesno.wav", "lentils.wav", "mom1.wav", "mom2.wav", 
            "illness.wav", "earth.wav", "ball1.wav", "ball2.wav"),
  task3 = c("rainbow_passage.wav"),
  task4 = c("oe.wav", "pa.wav", "pataka.wav", "ta.wav", "ka.wav", "kala.wav", "aui.wav"),
  task5 = c("f_autoind.wav", "f_bat.wav", "f_bicycle.wav", "f_cinema.wav", "f_cockroachkiller.wav", "f_mailman.wav", 
            "f_pastrychef.wav", "f_radio.wav", "f_ring.wav", "f_rose.wav", "f_safe.wav", "f_snail.wav", 
            "f_spaceship.wav", "f_telecom.wav", "s_autoind.wav", "s_bat.wav", "s_bicycle.wav", "s_cinema.wav", 
            "s_cockroachkiller.wav", "s_mailman.wav", "s_pastrychef.wav", "s_radio.wav", "s_ring.wav", 
            "s_rose.wav", "s_safe.wav", "s_snail.wav", "s_spaceship.wav", "s_telecom.wav"),
  task6 = c("counting.wav"),
  task7 = c("breathing.wav"),
  task8 = c("coughing.wav")
)


# --- 3. Αρχικοποίηση Data Frames για την Αποθήκευση Αποτελεσμάτων ---
#Πίνακας συνοψής για tasks (excel)
task_summary <- data.frame(
  Task = names(tasks),
  Exercises = sapply(tasks, function(x) paste(x, collapse = ", "))
)

#Τελικός πίνακας αποτελεσμάτων (excel)
final_results <- data.frame()

# --- 4. Κύριος Βρόχος Ανάλυσης ---
# ** Εξωτερικός Βρόχος: Επανάληψη για κάθε εξαρτημένη μεταβλητή **
for (dep_var in dependent_variables) {
  cat("Running models for dependent variable:", dep_var, "\n") 
  
  # Προσθήκη στην τελική συνοπτική αναφορά (excel) για να ξεχωριζουμε για ποιο ερώτηματα είναι τα αποτελέσματα
  final_results <- bind_rows(final_results, data.frame(
    Task = paste("--------Analysis for", dep_var, "--------"), 
    Predictor = NA, 
    Estimate = NA, 
    Std.Error = NA, 
    t.value = NA, 
    p.value = NA
  ))

# ** Μεσαίος Βρόχος: Επανάληψη για κάθε καθορισμένο task **
  for (task_name in names(tasks)) {
    file_names <- tasks[[task_name]]
    cat("Running model for task", task_name, "(", paste(file_names, collapse = ", "), ")\n")
    
    # === 4α. ΜΟΝΤΕΛΟ ΓΙΑ ΟΛΟΚΛΗΡΟ ΤΟ TASK (ΟΛΕΣ ΟΙ ΑΣΚΗΣΕΙΣ ΤΟΥ TASK ΣΥΝΔΥΑΣΤΙΚΑ) ===
    # Φιλτράρισμα δεδομένων
    filtered_data <- filter_data(data, file_names = file_names)
    
    #Εάν δεν υπάρχουν δεδομένα, προχωρήστε στο επόμενο task
    if (nrow(filtered_data) == 0) {
      cat("No data available for task", task_name, "\n")
      final_results <- bind_rows(final_results, data.frame(Task = task_name, Predictor = NA, Estimate = NA, Std.Error = NA, t.value = NA, p.value = NA))
      next
    }
    
    # Προεπεξεργασία της εξαρτημένης μεταβλητής ανάλογα με τον τύπο της. Αυτό είναι κρίσιμο για τη σωστή προσαρμογή του μοντέλου.
    if (dep_var == "H_Y_binary") {
    # Μετατροπή της βαθμολογίας Hoehn & Yahr σε δυαδική μεταβλητή (0 για < 3, 1 για >= 3)
      filtered_data$H_Y_binary <- ifelse(filtered_data$`H&Y` < 3, 0, 1)
    } else if (dep_var == "Fluctuations") {
    # Μετατροπή των "Yes"/"No" σε δυαδική μεταβλητή 1/0.
      filtered_data$Fluctuations <- ifelse(filtered_data$`Fluctuations` == "Yes", 1, 0)
    } else if (dep_var == "Dyskinesia") {
    # Μετατροπή των "Yes"/"No" σε δυαδική μεταβλητή 1/0.
      filtered_data$Dyskinesia <- ifelse(filtered_data$`Dyskinesia` == "Yes", 1, 0)
    } else if (dep_var == "UPDRS_III_dif_class") {
    # Μετατροπή της κατηγορικής μεταβλητής σε διατεταγμένη αριθμητική μεταβλητή.
      filtered_data$UPDRS_III_dif_class <- as.numeric(factor(filtered_data$UPDRS_III_dif_class, levels = c("Poor", "Suboptimal", "Excellent")))
    } else if (dep_var == "UPDRS_III_dif_per") {
      # Διασφάλιση η στήλη UPDRS_III_dif_per είναι ποσοτική (όπως μας ζητάει να την εξετάσουμε)
      if (!("UPDRS_III_dif_per" %in% colnames(filtered_data))) {
        cat("No data available for UPDRS_III_dif_per in task", task_name, "\n")
        final_results <- bind_rows(final_results, data.frame(Task = task_name, Predictor = NA, Estimate = NA, Std.Error = NA, t.value = NA, p.value = NA))
        next
      } else {
        filtered_data$UPDRS_III_dif_per <- as.numeric(filtered_data$UPDRS_III_dif_per)
      }
    }
    
    # Επιλογή των χαρακτηριστικών (features) από τις στήλες 24 έως 111 --> ολα τα χαρακτηριστικά
    features <- filtered_data[, 24:111]
    
    # Έγκυρα ονόματα μεταβλητών για R
    colnames(features) <- make.names(colnames(features))
    
    # Επαλήθευση ύπαρξης των predictor columns
    valid_predictors <- colnames(features)[colnames(features) %in% names(filtered_data)]
    
    # Χρήση valid predictors
    features <- features[, valid_predictors, drop = FALSE]
    
    # Δημιουργία formula για το μοντέλο
    predictors <- paste(valid_predictors, collapse = " + ")
    
    # Κατασκευή του πλήρους τύπου (formula) για το Γραμμικό Μικτό Μοντέλο (LMM).
    # Αυτός ο τύπος προβλέπει την εξαρτημένη μεταβλητή χρησιμοποιώντας όλα τα features ως fixed effects (σταθερές επιδράσεις).
    # Το "(1 | file_name)" ορίζει ένα random intercept (τυχαία επίδραση στην τιμή εκκίνησης) για το 'file_name'.
    # Αυτό είναι σημαντικό διότι λαμβάνει υπόψη τη μη-ανεξαρτησία των σημείων δεδομένων που προέρχονται από διαφορετικές
    # ασκήσεις μέσα στο ίδιο task (δηλαδή, κάποιες ασκήσεις μπορεί να έχουν συστηματικά υψηλότερες/χαμηλότερες τιμές).
    formula <- as.formula(paste(dep_var, "~", predictors, "+ (1 | file_name)"))
    
    # Χρήση του tryCatch για την προσαρμογή του μοντέλου. Αυτό θα "πιάσει" οποιοδήποτε σφάλμα (π.χ. αν το μοντέλο
    # αποτύχει να συγκλίνει) χωρίς να σταματήσει ολόκληρο το script, κάνοντας την ανάλυση πιο ανθεκτική.
    model <- tryCatch(
      lmer(formula, data = filtered_data),
      error = function(e) {
        cat("Error in model fitting for task", task_name, ":", e$message, "\n")
        return(NULL)
      }
    )
    
    # Αν το μοντέλο εφαρμόστηκε επιτυχώς
    if (!is.null(model)) {
      # Εκτύπωση συνοψής του μοντέλου
      model_summary <- summary(model)
      
      # Εξαγωγή συντελεστών και p-values
      fixed_effects <- model_summary$coefficients
      
      # Μορφοποίηση των αποτελεσμάτων (για fixed effects output)
      fixed_results_df <- data.frame(
        Task = paste(task_name, "(All)"), 
        Predictor = rownames(fixed_effects),
        Estimate = fixed_effects[, "Estimate"],
        Std.Error = fixed_effects[, "Std. Error"],
        t.value = fixed_effects[, "t value"],
        p.value = fixed_effects[, "Pr(>|t|)"]
      )
      
      final_results <- bind_rows(final_results, fixed_results_df)
      
      # Προσθήκη κενής γραμμής στην τελική αναφορά για καλύτερη εμφάνιση στο Excel
      final_results <- bind_rows(final_results, data.frame(Task = NA, Predictor = NA, Estimate = NA, Std.Error = NA, t.value = NA, p.value = NA))
      
      # Αριθμός παρατηρήσεων που χρησιμοποιήθηκαν στο μοντέλο
      cat("Number of observations used in the model:", nobs(model), "\n")
      cat("Model summary:\n")
      print(model_summary)
    } else {
      cat("Model could not be fitted for task", task_name, "\n")
      final_results <- bind_rows(final_results, data.frame(Task = task_name, Predictor = NA, Estimate = NA, Std.Error = NA, t.value = NA, p.value = NA))
    }
    
    # === 4β. Εσωτερικός Βρόχος: ΜΟΝΤΕΛΟ ΓΙΑ ΚΑΘΕ ΜΕΜΟΝΩΜΕΝΗ ΑΣΚΗΣΗ ΕΝΤΟΣ ΤΟΥ TASK ===
    for (file_name in file_names) {
      cat("Running model for individual exercise:", file_name, "\n")
      filtered_data <- filter_data(data, file_names = file_name)
      
      # Αν δεν υπάρχουν δεδομένα, προχωρήστε στην επόμενη υποάσκηση
      if (nrow(filtered_data) == 0) {
        cat("No data available for exercise", file_name, "\n")
        final_results <- bind_rows(final_results, data.frame(Task = file_name, Predictor = NA, Estimate = NA, Std.Error = NA, t.value = NA, p.value = NA))
        next
      }
      
    # --- Επανάληψη των ίδιων βημάτων προεπεξεργασίας για τα δεδομένα της μίας άσκησης ---
      if (dep_var == "H_Y_binary") {
        filtered_data$H_Y_binary <- ifelse(filtered_data$`H&Y` < 3, 0, 1)
      } else if (dep_var == "Fluctuations") {
        filtered_data$Fluctuations <- ifelse(filtered_data$`Fluctuations` == "Yes", 1, 0)
      } else if (dep_var == "Dyskinesia") {
        filtered_data$Dyskinesia <- ifelse(filtered_data$`Dyskinesia` == "Yes", 1, 0)
      } else if (dep_var == "UPDRS_III_dif_class") {
        filtered_data$UPDRS_III_dif_class <- as.numeric(factor(filtered_data$UPDRS_III_dif_class, levels = c("Poor", "Suboptimal", "Excellent")))
      } else if (dep_var == "UPDRS_III_dif_per") {
        # Διασφαλίζουμε ότι η στήλη UPDRS_III_dif_per υπάρχει και είναι ποσοτική
        if (!("UPDRS_III_dif_per" %in% colnames(filtered_data))) {
          cat("No data available for UPDRS_III_dif_per in exercise", file_name, "\n")
          final_results <- bind_rows(final_results, data.frame(Task = file_name, Predictor = NA, Estimate = NA, Std.Error = NA, t.value = NA, p.value = NA))
          next
        } else {
          filtered_data$UPDRS_III_dif_per <- as.numeric(filtered_data$UPDRS_III_dif_per)
        }
      }
      
      # Επιλογή χαρακτηριστικών (features) από τις στήλες 24 έως 111
      features <- filtered_data[, 24:111]
      
      # Έγκυρα ονόματα μεταβλητών για R
      colnames(features) <- make.names(colnames(features))
      
      # Επαλήθευση ύπαρξης των predictor columns
      valid_predictors <- colnames(features)[colnames(features) %in% names(filtered_data)]
      
      # Χρήση των valid predictors
      features <- features[, valid_predictors, drop = FALSE]
      
      # Δημιουργία formula για το μοντέλο
      predictors <- paste(valid_predictors, collapse = " + ")
      
      if (length(unique(filtered_data$file_name)) < 2) {
        # Χρήση απλού γραμμικού μοντέλου (LM) αν υπάρχει μόνο ένα επίπεδο του τυχαίου αποτελέσματος
        formula <- as.formula(paste(dep_var, "~", predictors))
        model <- tryCatch(
          lm(formula, data = filtered_data),
          error = function(e) {
            cat("Error in model fitting for exercise", file_name, ":", e$message, "\n")
            return(NULL)
          }
        )
      } else {
        # Χρήση LMM αν υπάρχουν πολλαπλά επίπεδα του τυχαίου αποτελέσματος
        formula <- as.formula(paste(dep_var, "~", predictors, "+ (1 | file_name)"))
        model <- tryCatch(
          lmer(formula, data = filtered_data),
          error = function(e) {
            cat("Error in model fitting for exercise", file_name, ":", e$message, "\n")
            return(NULL)
          }
        )
      }
      
      # Αν το μοντέλο εφαρμόστηκε επιτυχώς
      if (!is.null(model)) {
        # Εκτύπωση συνοψής του μοντέλου
        model_summary <- summary(model)
        
        # Εξαγωγή συντελεστών και p-values
        fixed_effects <- if (inherits(model, "lm")) {
          coef(summary(model))
        } else {
          model_summary$coefficients
        }
        
        # Μορφοποίηση για fixed effects output
        fixed_results_df <- data.frame(
          Task = file_name, 
          Predictor = rownames(fixed_effects),
          Estimate = fixed_effects[, "Estimate"],
          Std.Error = fixed_effects[, "Std. Error"],
          t.value = fixed_effects[, "t value"],
          p.value = fixed_effects[, "Pr(>|t|)"]
        )
        
        final_results <- bind_rows(final_results, fixed_results_df)
        
        # Προσθήκη κενής γραμμής στην τελική αναφορά για καλύτερη εμφάνιση στο Excel
        final_results <- bind_rows(final_results, data.frame(Task = NA, Predictor = NA, Estimate = NA, Std.Error = NA, t.value = NA, p.value = NA))
        
        # Αριθμός παρατηρήσεων που χρησιμοποιήθηκαν στο μοντέλο
        cat("Number of observations used in the model:", nobs(model), "\n")
        cat("Model summary:\n")
        print(model_summary)
      } else {
        cat("Model could not be fitted for exercise", file_name, "\n")
        final_results <- bind_rows(final_results, data.frame(Task = file_name, Predictor = NA, Estimate = NA, Std.Error = NA, t.value = NA, p.value = NA))
      }
    }
  }
}
    
# --- 5. Αποθήκευση Τελικών Αποτελεσμάτων ---
# Γράψιμο των τελικών αποτελεσμάτων σε αρχείο Excel
output_file_path <- "summary_all.xlsx"
write_xlsx(list("Task Summary" = task_summary, "Model Results" = final_results), output_file_path)


Running models for dependent variable: H_Y_binary 
Running model for task task1 ( a1.wav, a2.wav, a3.wav, z1.wav, z2.wav, z3.wav, s1.wav, s2.wav, s3.wav )


Warning message:
“Some predictor variables are on very different scales: consider rescaling”
boundary (singular) fit: see help('isSingular')

Warning message:
“Some predictor variables are on very different scales: consider rescaling”


Number of observations used in the model: 1566 
Model summary:
Linear mixed model fit by REML. t-tests use Satterthwaite's method [
lmerModLmerTest]
Formula: formula
   Data: filtered_data

REML criterion at convergence: 2243.5

Scaled residuals: 
    Min      1Q  Median      3Q     Max 
-1.8664 -0.6648 -0.3438  0.7258  3.3550 

Random effects:
 Groups    Name        Variance Std.Dev.
 file_name (Intercept) 0.0000   0.0000  
 Residual              0.1641   0.4052  
Number of obs: 1566, groups:  file_name, 9

Fixed effects:
                                                 Estimate Std. Error         df
(Intercept)                                     9.818e-01  2.533e-01  1.489e+03
F0semitoneFrom27.5Hz_sma3nz_amean               2.568e-02  1.493e-02  1.489e+03
F0semitoneFrom27.5Hz_sma3nz_stddevNorm          7.893e-01  2.759e-01  1.489e+03
F0semitoneFrom27.5Hz_sma3nz_percentile20.0     -6.220e-03  5.314e-03  1.489e+03
F0semitoneFrom27.5Hz_sma3nz_percentile50.0     -3.229e-03  5.124e-03  1


Correlation matrix not shown by default, as p = 77 > 12.
Use print(model_summary, correlation=TRUE)  or
    vcov(model_summary)        if you need it




fit warnings:
Some predictor variables are on very different scales: consider rescaling
optimizer (nloptwrap) convergence code: 0 (OK)
boundary (singular) fit: see help('isSingular')

Running model for individual exercise: a1.wav 
Number of observations used in the model: 174 
Model summary:

Call:
lm(formula = formula, data = filtered_data)

Residuals:
     Min       1Q   Median       3Q      Max 
-0.66351 -0.21195 -0.05218  0.14231  0.96446 

Coefficients:
                                                 Estimate Std. Error t value
(Intercept)                                     2.280e+00  2.422e+00   0.941
F0semitoneFrom27.5Hz_sma3nz_amean              -2.435e-01  1.638e-01  -1.487
F0semitoneFrom27.5Hz_sma3nz_stddevNorm          3.631e-01  2.019e+00   0.180
F0semitoneFrom27.5Hz_sma3nz_percentile20.0      5.997e-02  4.974e-02   1.206
F0semitoneFrom27.5Hz_sma3nz_percentile50.0      1.390e-01  6.717e-02   2.070
F0semitoneFrom27.5Hz_sma3nz_percentile80.0      3.706e-02  9.322e-02   0.39

...

Number of observations used in the model: 153 
Model summary:

Call:
lm(formula = formula, data = filtered_data)

Residuals:
    Min      1Q  Median      3Q     Max 
-38.418  -5.958   0.531   6.388  37.563 

Coefficients:
                                                 Estimate Std. Error t value
(Intercept)                                     1.354e+02  2.731e+02   0.496
F0semitoneFrom27.5Hz_sma3nz_amean               1.258e+00  3.928e+00   0.320
F0semitoneFrom27.5Hz_sma3nz_stddevNorm          2.377e+01  6.060e+01   0.392
F0semitoneFrom27.5Hz_sma3nz_percentile20.0     -9.117e-01  1.826e+00  -0.499
F0semitoneFrom27.5Hz_sma3nz_percentile50.0     -8.420e-01  1.596e+00  -0.528
F0semitoneFrom27.5Hz_sma3nz_percentile80.0     -3.040e-01  1.281e+00  -0.237
F0semitoneFrom27.5Hz_sma3nz_meanRisingSlope     4.170e-02  2.828e-02   1.474
F0semitoneFrom27.5Hz_sma3nz_stddevRisingSlope  -3.418e-02  3.133e-02  -1.091
F0semitoneFrom27.5Hz_sma3nz_meanFallingSlope   -7.966e-03  1.208e-02  -0.660
F0semito

Warning message in eval(expr, envir, enclos):
“NAs introduced by coercion”


Error in model fitting for task task8 : grouping factors must have > 1 sampled level 
Model could not be fitted for task task8 
Running model for individual exercise: coughing.wav 


Warning message in eval(expr, envir, enclos):
“NAs introduced by coercion”


Number of observations used in the model: 153 
Model summary:

Call:
lm(formula = formula, data = filtered_data)

Residuals:
    Min      1Q  Median      3Q     Max 
-42.004  -8.985   1.222   8.638  45.519 

Coefficients:
                                                 Estimate Std. Error t value
(Intercept)                                    -57.047499 102.000587  -0.559
F0semitoneFrom27.5Hz_sma3nz_amean               -4.953516   2.486304  -1.992
F0semitoneFrom27.5Hz_sma3nz_stddevNorm         -62.520044  56.920724  -1.098
F0semitoneFrom27.5Hz_sma3nz_percentile20.0       0.472921   1.243155   0.380
F0semitoneFrom27.5Hz_sma3nz_percentile50.0       1.085382   1.071076   1.013
F0semitoneFrom27.5Hz_sma3nz_percentile80.0       1.629163   1.116408   1.459
F0semitoneFrom27.5Hz_sma3nz_meanRisingSlope      0.005620   0.016624   0.338
F0semitoneFrom27.5Hz_sma3nz_stddevRisingSlope   -0.006917   0.018531  -0.373
F0semitoneFrom27.5Hz_sma3nz_meanFallingSlope     0.043382   0.014436   3.005
F0semito